In [1]:
#%matplotlib inline
#%load_ext autoreload
#%autoreload 2

In [2]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [3]:
# Matlab-like way to work with matrices
import numpy as np
from numpy import genfromtxt
from tqdm.notebook import tqdm
import scipy

# R-like way to work with dataframes
import pandas as pd

# Equivalent of brainstorm, EEGLAB, ...
import mne
from mne.io import read_raw_eeglab
from mne.viz import plot_topomap
from mne.channels import make_eeg_layout
from mne.preprocessing import compute_proj_eog
from mne.viz import circular_layout, plot_connectivity_circle
from mne.connectivity import spectral_connectivity

# Plotting libraries
import matplotlib.pylab as plt   # <= Similar to Matlab
import seaborn as sns            # <= Easy, nice-looking plotting  

from eegip.utils import loadmat # load_montage, 
from eegip.preprocessing import preprocess, channel_rejection, add_bad_segment_annot, \
    get_events, get_epochs, remove_rejected_ica_components, get_evoked
from eegip.dataset import DatasetMng
from eegip.path import get_path
from eegip import Analysis
from eegip.sources import SourcesBIDS

from sklearn.decomposition import PCA, FastICA
from mne.preprocessing import ICA

from warnings import warn
#from eegip.config import eegip_config
#from eegip.plotting import plot_mean_and_CI

# Others...
import xarray as xr
from pathlib import Path
import re
import os
from glob import glob

In [4]:
dataset_name="eegip_london"
config =  {"atlas":{"vol_labels":[]}}

template_check_path = Path("/home/christian/template_check/")
dataset_mng = DatasetMng(config=[config], dataset_name=dataset_name)
recording_names = sorted([name for name in dataset_mng.dataset.recordings if "m12" not in name])

# Compute scalp stats

In [5]:
for recording_name in tqdm(recording_names):
    recording = dataset_mng.dataset.recordings[recording_name]

    try:
        recording.get_artifact("events", recompute=True)                
        recording.get_artifact("epochs", recompute=True)
    except FileNotFoundError as e:
        continue

    data = recording.epochs.get_data()
    
    data = xr.DataArray(data, dims=('epochs', 'channels', 'times'),
                     coords={'epochs': np.arange(data.shape[0]), 
                             'channels': recording.epochs.ch_names,
                             'times': recording.epochs.times})

    data -= data.mean("times")  # De-meaning time series
    
    inv_event_id = {val:key for key, val in recording.epochs.event_id.items()}
    event_strs = np.array([inv_event_id[id_] for id_ in recording.epochs.events[:, 2]])

    recording.flush()
        
    for event_str in np.unique(event_strs):
        epochs_no = np.where(event_strs == event_str)[0] 

        file_path = template_check_path / "{}_{}_{}_mean.netcdf".format(recording_name, event_str, "scalp")
        data.sel(epochs=epochs_no).mean("epochs").to_netcdf(file_path, mode= 'w')

        file_path = template_check_path / "{}_{}_{}_std.netcdf".format(recording_name, event_str, "scalp")
        data.sel(epochs=epochs_no).std("epochs").to_netcdf(file_path, mode= 'w')

Opening raw data file /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s601/ses-m06/eeg/sub-s601_ses-m06_eeg.fif...


/home/christian/synchedout/eegip/eegip/recording.py:210: RuntimeWarning: This filename (/home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s601/ses-m06/eeg/sub-s601_ses-m06_eeg.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz or _meg.fif
  self._preprocessed_raw = mne.io.read_raw_fif(self.get_path("preprocessed_raw"), verbose=self.verbose)


    Range : 0 ... 81499 =      0.000 ...   162.998 secs
Ready.
116 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Loading data for 116 events and 500 original time points ...
61 bad epochs dropped
Reading /media/christian/seagate/eegip/london/derivatives/lossless/sub-s602/ses-m06/eeg/sub-s602_ses-m06_eeg_qcr.fdt
Reading 0 ... 240999  =      0.000 ...   481.998 secs...
Setting up band-stop filter

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal bandstop filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower transition bandwidth: 0.50 Hz
- Upper transition bandwidth: 0.50 Hz
- Filter length: 3301 samples (6.602 sec)



/home/christian/synchedout/eegip/eegip/recording.py:557: UserWarning: No montage set. Using the default montage.
  warnings.warn("No montage set. Using the default montage.")


Filtering raw data in 1 contiguous segment
Setting up high-pass filter at 1 Hz

FIR filter parameters
---------------------
Designing a one-pass, zero-phase, non-causal highpass filter:
- Windowed time-domain design (firwin) method
- Hamming window with 0.0194 passband ripple and 53 dB stopband attenuation
- Lower passband edge: 1.00
- Lower transition bandwidth: 1.00 Hz (-6 dB cutoff frequency: 0.50 Hz)
- Filter length: 1651 samples (3.302 sec)

############ file_name /media/christian/seagate/eegip/london/derivatives/lossless/sub-s602/ses-m06/eeg/sub-s602_ses-m06_eeg_qcr.set <class 'str'>
############ raw_eeg dict_keys(['setname', 'filename', 'filepath', 'subject', 'group', 'condition', 'session', 'comments', 'nbchan', 'trials', 'pnts', 'srate', 'xmin', 'xmax', 'times', 'data', 'icaact', 'icawinv', 'icasphere', 'icaweights', 'icachansind', 'chanlocs', 'urchanlocs', 'chaninfo', 'ref', 'event', 'urevent', 'eventdescription', 'epoch', 'epochdescription', 'reject', 'stats', 'specdata', 's

...

Closing /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s750/ses-m06/eeg/sub-s750_ses-m06_eeg.fif [done]
Opening raw data file /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s750/ses-m06/eeg/sub-s750_ses-m06_eeg.fif...
    Range : 0 ... 228499 =      0.000 ...   456.998 secs
Ready.
Reading 0 ... 228499  =      0.000 ...   456.998 secs...


/home/christian/synchedout/eegip/eegip/recording.py:210: RuntimeWarning: This filename (/home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s750/ses-m06/eeg/sub-s750_ses-m06_eeg.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz or _meg.fif
  self._preprocessed_raw = mne.io.read_raw_fif(self.get_path("preprocessed_raw"), verbose=self.verbose)


Overwriting existing file.
Writing /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s750/ses-m06/eeg/sub-s750_ses-m06_eeg.fif


/home/christian/synchedout/eegip/eegip/recording.py:251: RuntimeWarning: This filename (/home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s750/ses-m06/eeg/sub-s750_ses-m06_eeg.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz or _meg.fif
  self._preprocessed_raw.save(path, overwrite=True)


Closing /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s750/ses-m06/eeg/sub-s750_ses-m06_eeg.fif [done]
374 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Loading data for 374 events and 500 original time points ...
95 bad epochs dropped



# Compute ICA stats

In [6]:
template = "ica"
for recording_name in tqdm(recording_names):            
    recording = dataset_mng.dataset.recordings[recording_name]

    try:
        recording.get_artifact("events", recompute=True)                
        recording.get_artifact("epochs", recompute=True)
    except FileNotFoundError as e:
        continue

    recording.montage = mne.channels.make_standard_montage("GSN-HydroCel-129")

    inv_event_id = {val:key for key, val in recording.epochs.event_id.items()}
    event_strs = np.array([inv_event_id[id_] for id_ in recording.epochs.events[:, 2]])

    for event_str in np.unique(event_strs):
        ica = ICA(method='fastica', random_state=324234)
        ica = ica.fit(recording.epochs[event_str], verbose=False)
        ica_comp = ica.get_components()

        data = recording.epochs[event_str].get_data(picks="eeg").transpose([0, 2, 1]) @ ica_comp 
        recording.flush()        
        
        data = xr.DataArray(data, dims=('epochs', 'times', 'components'),
                         coords={'epochs': np.arange(data.shape[0]), 
                                 'components': np.arange(data.shape[2]),
                                 'times': recording.epochs.times})

        data -= data.mean("times")  # De-meaning time series

        file_path = template_check_path / "{}_{}_{}_mean.netcdf".format(recording_name, event_str, template)
        data.mean("epochs").to_netcdf(file_path, mode= 'w')

        file_path = template_check_path / "{}_{}_{}_std.netcdf".format(recording_name, event_str, template)
        data.std("epochs").to_netcdf(file_path, mode= 'w')

    recording.flush()

Opening raw data file /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s601/ses-m06/eeg/sub-s601_ses-m06_eeg.fif...


/home/christian/synchedout/eegip/eegip/recording.py:210: RuntimeWarning: This filename (/home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s601/ses-m06/eeg/sub-s601_ses-m06_eeg.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz or _meg.fif
  self._preprocessed_raw = mne.io.read_raw_fif(self.get_path("preprocessed_raw"), verbose=self.verbose)


    Range : 0 ... 81499 =      0.000 ...   162.998 secs
Ready.
116 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Loading data for 116 events and 500 original time points ...
61 bad epochs dropped
Overwriting existing file.
Reading /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s601/ses-m06/mod/sub-s601_ses-m06_epo.fif ...
    Found the data of interest:
        t =    -200.00 ...     798.00 ms
        0 CTF compensation matrices available
55 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Reading /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s601/ses-m06/mod/sub-s601_ses-m06_epo.fif ...
    Found the data of interest:
        t =    -200.00 ...     798.00 ms
        0 CTF compensation matrices available
55 matching events found
No baseline correction applied
Not sett

/home/christian/synchedout/eegip/eegip/recording.py:210: RuntimeWarning: This filename (/home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s602/ses-m06/eeg/sub-s602_ses-m06_eeg.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz or _meg.fif
  self._preprocessed_raw = mne.io.read_raw_fif(self.get_path("preprocessed_raw"), verbose=self.verbose)


    Range : 0 ... 240999 =      0.000 ...   481.998 secs
Ready.
374 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Loading data for 374 events and 500 original time points ...
146 bad epochs dropped
Overwriting existing file.
Reading /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s602/ses-m06/mod/sub-s602_ses-m06_epo.fif ...
    Found the data of interest:
        t =    -200.00 ...     798.00 ms
        0 CTF compensation matrices available
228 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Reading /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s602/ses-m06/mod/sub-s602_ses-m06_epo.fif ...
    Found the data of interest:
        t =    -200.00 ...     798.00 ms
        0 CTF compensation matrices available
228 matching events found
No baseline correction applied
Not 

...

    Range : 0 ... 287499 =      0.000 ...   574.998 secs
Ready.
440 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Loading data for 440 events and 500 original time points ...
159 bad epochs dropped
Overwriting existing file.
Reading /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s748/ses-m06/mod/sub-s748_ses-m06_epo.fif ...
    Found the data of interest:
        t =    -200.00 ...     798.00 ms
        0 CTF compensation matrices available
281 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Reading /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s748/ses-m06/mod/sub-s748_ses-m06_epo.fif ...
    Found the data of interest:
        t =    -200.00 ...     798.00 ms
        0 CTF compensation matrices available
281 matching events found
No baseline correction applied
Not 

/home/christian/synchedout/eegip/eegip/recording.py:210: RuntimeWarning: This filename (/home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s749/ses-m06/eeg/sub-s749_ses-m06_eeg.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz or _meg.fif
  self._preprocessed_raw = mne.io.read_raw_fif(self.get_path("preprocessed_raw"), verbose=self.verbose)


    Range : 0 ... 254499 =      0.000 ...   508.998 secs
Ready.
419 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Loading data for 419 events and 500 original time points ...
138 bad epochs dropped
Overwriting existing file.
Reading /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s749/ses-m06/mod/sub-s749_ses-m06_epo.fif ...
    Found the data of interest:
        t =    -200.00 ...     798.00 ms
        0 CTF compensation matrices available
281 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Reading /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s749/ses-m06/mod/sub-s749_ses-m06_epo.fif ...
    Found the data of interest:
        t =    -200.00 ...     798.00 ms
        0 CTF compensation matrices available
281 matching events found
No baseline correction applied
Not 

/home/christian/synchedout/eegip/eegip/recording.py:210: RuntimeWarning: This filename (/home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s750/ses-m06/eeg/sub-s750_ses-m06_eeg.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz or _meg.fif
  self._preprocessed_raw = mne.io.read_raw_fif(self.get_path("preprocessed_raw"), verbose=self.verbose)


    Range : 0 ... 228499 =      0.000 ...   456.998 secs
Ready.
374 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Loading data for 374 events and 500 original time points ...
95 bad epochs dropped
Overwriting existing file.
Reading /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s750/ses-m06/mod/sub-s750_ses-m06_epo.fif ...
    Found the data of interest:
        t =    -200.00 ...     798.00 ms
        0 CTF compensation matrices available
279 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Reading /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s750/ses-m06/mod/sub-s750_ses-m06_epo.fif ...
    Found the data of interest:
        t =    -200.00 ...     798.00 ms
        0 CTF compensation matrices available
279 matching events found
No baseline correction applied
Not s

# Compute fsaverage stats

In [7]:
subject_dir = Path(os.environ["SUBJECTS_DIR"])

recompute_smodel = False
recompute_fmodel = False
recompute_sources = False
model_type="average"
inv_method="dSPM"
snr=1.0
lambda2=None

template = "fsaverage"
fs_subject = template
derivative_name="template_validation_" + template
for recording_name in tqdm(recording_names):    
    recording = dataset_mng.dataset.recordings[recording_name]

    try:
        recording.get_artifact("events", recompute=True)                
        recording.get_artifact("epochs", recompute=True)
    except FileNotFoundError as e:
        continue

    recording.montage = mne.channels.make_standard_montage("GSN-HydroCel-129")

    smodel = recording.subject.add_smodel(name=fs_subject, fs_subject=fs_subject,
                                          type_=model_type, exists="return")
    if recompute_smodel:
        smodel.recompute()

    print(fs_subject)
    fmodel = recording.add_fmodel(smodel, name=fs_subject, exists="return")
    #if fname_trans is not None:
    #    fmodel.fname_trans = fname_trans
    if recompute_fmodel:
        try:
            fmodel.recompute()
        except FileNotFoundError as e:
            print(e)
            print("Skipping {}. It seems not to be available in lossless qcr version.".format(recording_name))
            continue

    if dataset_mng.dataset_config["is_bids"]:
        sources = SourcesBIDS(fmodel, snr=snr, lambda2=lambda2, method=inv_method,
                              derivative_name=derivative_name)
    else:
        sources = Sources(fmodel, snr=snr, lambda2=lambda2, method=inv_method)

    if recompute_sources:            
        sources.get_data(recompute=True, type_="all")


    # Save label stats
    sources.compute_labels(recompute=recompute_sources, no_epochs=None)

    data = sources.get_data(type_="labels")            


    data -= data.mean("times")  # De-meaning time series

    inv_event_id = {val:key for key, val in recording.epochs.event_id.items()}
    event_strs = np.array([inv_event_id[id_] for id_ in recording.epochs.events[:, 2]])    
    
    recording.flush()
    fmodel.flush()
    sources.flush()

    for event_str in np.unique(event_strs):
        epochs_no = np.where(event_strs == event_str)[0] 

        file_path = template_check_path / "{}_{}_{}_mean.netcdf".format(recording_name, event_str, template)
        data.sel(epochs=epochs_no).mean("epochs").to_netcdf(file_path, mode= 'w')

        file_path = template_check_path / "{}_{}_{}_std.netcdf".format(recording_name, event_str, template)
        data.sel(epochs=epochs_no).std("epochs").to_netcdf(file_path, mode= 'w')

    # Removing full source from the hard drive for space reasons 
    sources.delete_sources()
    
    # No need to recompute the smodel for every recordings since it does not depend on the 
    # recording
    recompute_smodel = False         


Opening raw data file /home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s601/ses-m06/eeg/sub-s601_ses-m06_eeg.fif...


/home/christian/synchedout/eegip/eegip/recording.py:210: RuntimeWarning: This filename (/home/christian/synchedout/eegip/eegip/tests/test_artifacts/derivatives/eegip_london_preprocessed/sub-s601/ses-m06/eeg/sub-s601_ses-m06_eeg.fif) does not conform to MNE naming conventions. All raw files should end with raw.fif, raw_sss.fif, raw_tsss.fif, raw.fif.gz, raw_sss.fif.gz, raw_tsss.fif.gz or _meg.fif
  self._preprocessed_raw = mne.io.read_raw_fif(self.get_path("preprocessed_raw"), verbose=self.verbose)


    Range : 0 ... 81499 =      0.000 ...   162.998 secs
Ready.
116 matching events found
No baseline correction applied
Not setting metadata
0 projection items activated
Loading data for 116 events and 500 original time points ...
61 bad epochs dropped
Overwriting existing file.
fsaverage
Computing rank from data with rank=None
    Using tolerance 1.6e-10 (2.2e-16 eps * 118 dim * 6.2e+03  max singular value)
    Estimated rank (eeg): 118
    EEG: rank 118 computed from 118 data channels with 0 projectors
Reducing data rank from 118 -> 118
Estimating covariance using SHRUNK
Done.
Estimating covariance using DIAGONAL_FIXED
    EEG regularization : 0.1
Done.
Estimating covariance using EMPIRICAL
Done.
Using cross-validation to select the best estimator.
    EEG regularization : 0.1
    EEG regularization : 0.1
    EEG regularization : 0.1
Number of samples used : 5555
log-likelihood on unseen data (descending order):
   shrunk: -245.083
   diagonal_fixed: -379.209
   empirical: -1081.868


/home/christian/synchedout/eegip/eegip/functionalmodel.py:102: UserWarning: Using no transform to align the sensors to the head. This is not recommended.
  warnings.warn("Using no transform to align the sensors to the head. This is not recommended.")


    Reading a source space...
    Computing patch statistics...
    Patch information added...
    Distance information added...
    [done]
    Reading a source space...
    Computing patch statistics...
    Patch information added...
    Distance information added...
    [done]
    2 source spaces read
    3 BEM surfaces found
    Reading a surface...
[done]
    Reading a surface...
[done]
    Reading a surface...
[done]
    3 BEM surfaces read
Loading surfaces...
Three-layer model surfaces loaded.

Loading the solution matrix...

Loaded linear_collocation BEM solution from /media/christian/seagate/eegip/london/derivatives/smodel_fsaverage/fsaverage_bem
BEM              : <ConductorModel  |  BEM (3 layers)>
grid                  : 5.0 mm
mindist               : 5.0 mm
MRI volume            : /usr/local/freesurfer/subjects/fsaverage/mri/aseg.mgz

Taking inner skull from <ConductorModel  |  BEM (3 layers)>

Overwriting existing file.
    0 source spaces written
Source space          : <

...

Processing epoch : 278 / 279
combining the current components...


278it [00:57,  4.69it/s]

Processing epoch : 279 / 279
combining the current components...


279it [00:57,  4.81it/s]


Applying sign flip for label grouping.

